In [42]:
import sys
import operator
import re
import json
import nltk  # needed for
# nltk.download('punkt') #getting libraries
# nltk.download('stopwords')
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer

outfile="output.json"
queriesFile="queries.txt"
IndexFile="input_corpus.txt"

ps = PorterStemmer()
stopwords = set(stopwords.words('english'))


def word_tokenize(line):
    return re.split(r'[\s-]+', line)


def ExtractLine(line):
    data = line.split('\t')
    if len(data) < 1:
        return None
    return data[0], data[1]


def CleanLine(line):
    return re.sub(r'[^a-z\s0-9-]', ' ', line.strip().lower())


def StemWords(words):
    stemmed = []
    for word in words:
        stem = ps.stem(word)
        if stem in stemmed:
            continue
        stemmed.append(stem)
    return stemmed


def RemoveStopWords(words):
    return [x for x in words if x not in stopwords]


def ReadInput(filename):
    file1 = open(filename, 'r+', encoding="utf8")
    Lines = file1.readlines()
    file1.close()
    return Lines


def main():
    linked_list = ProcessLibrary()
    #  print(linked_list.traverse_list())
    # print(GetIndexesOfstemmedWord("etiopathogenesi", linked_list))
    SearchWords = ProcessSearch()
    Searches = ConvertSearchesIntoIndex(SearchWords, linked_list)
    with open(outfile, 'w') as outfilePointer:
        json.dump(Searches, outfilePointer)
    #print(json.dumps(Searches))


def ProcessSingleSearch(SearchWordList, linked_list):
    MaxDocId = -1
    MinDocId = -1
    Indexes = []
    for word in SearchWordList:
        Stimpack = GetIndexesOfstemmedWord(word, linked_list)
        Indexes.append([word, Stimpack])
        if MinDocId == -1:
            MinDocId = Stimpack[0]
        elif MinDocId > Stimpack[0]:
            MinDocId = Stimpack[0]
        if MaxDocId == -1:
            MaxDocId = Stimpack[-1]
        elif Stimpack[-1] < MaxDocId:
            MaxDocId = Stimpack[-1]
    for IndexList in Indexes:
        IndexList[1] = set(filter(lambda e: e >= MinDocId and e <= MaxDocId, IndexList[1]))
    return Indexes


def ConvertSearchesIntoIndex(SearchWords, linked_list):
    jsonData = dict()
    jsonData["postingsList"] = dict()
    jsonData["daatAnd"] = dict()
    for SearchWordListItems in SearchWords:
        SearchWordList = SearchWordListItems[0]
        Indexes = ProcessSingleSearch(SearchWordList, linked_list)
        for Index in Indexes:
            res = list(Index[1])
            res.sort()
            jsonData["postingsList"][Index[0]] = res

        JustIndexes = map(lambda x: x[1], Indexes)
        Compares = 0
        for i in Indexes:
            Compares += len(i[1])
        InterSects = list(set.intersection(*JustIndexes))
        InterSects.sort()

        SearchPhrase = SearchWordListItems[1]
        jsonData["daatAnd"][SearchPhrase] = dict()
        jsonData["daatAnd"][SearchPhrase]["results"] = InterSects
        jsonData["daatAnd"][SearchPhrase]["num_docs"] = len(InterSects)
        jsonData["daatAnd"][SearchPhrase]["num_comparisons"] = Compares
    return jsonData

def ProcessSearch():
    Lines = ReadInput(queriesFile)
    Data = []
    for line in Lines:
        print("Input query -> ",line)
        WordString = CleanLine(line)
        print("Query Post Processing -> ",WordString)
        cleaned_line = CleanLine(WordString)
        tokens = word_tokenize(cleaned_line)
        print("Doc tokens post whitespace tokenizing -> ",tokens)
        t = RemoveStopWords(tokens)
        print("Doc tokens post stopword removal -> ",t)
        stemmed = StemWords(t)
        print("Doc tokens post stemming -> ",stemmed,"\n")
        Data.append([stemmed, line.strip()])
    return Data


def ProcessLibrary():
    linked_list = LinkedList()
    Lines = ReadInput(IndexFile)
    Data = []
    maps = dict()
    for line in Lines:
        print("Input -> ",line)
        docId, WordString = ExtractLine(line)
        print ("Doc id -> "+docId)
        print("Doc text -> "+WordString+"\n")
        if docId is None:
            continue
        cleaned_line = CleanLine(WordString)
        print("Doc text post processing -> ",cleaned_line,"\n") 
        tokens = word_tokenize(cleaned_line)
        print("Doc tokens post whitespace tokenizing -> ",tokens)
        t = RemoveStopWords(tokens)
        print("Doc tokens post stopword removal -> ",t)
        stemmed = StemWords(t)
        print("Doc tokens post stemming -> ",stemmed,"\n")
        Data.append([int(docId), stemmed])
    sorted_list = sorted(Data, key=operator.itemgetter(0))
    for doc in sorted_list:
        DocID = doc[0]
        Words = doc[1]
        for word in Words:
            if word not in maps.keys():
                maps[word] = []
            if DocID not in maps[word]:
                maps[word].append(DocID)
    for word in maps.keys():
        linked_list.insert_at_end([word, maps[word]])
    return linked_list


def GetIndexesOfstemmedWord(word, linkedList):
    start = linkedList.start_node
    while start is not None:
        if start.value[0] == word:
            return start.value[1]
        start = start.next
    return None

class Node:
    def __init__(self, value = None, next = None):
        self.value = value
        self.next = next

class LinkedList:

    def __init__(self, index=0, mode="simple"):
        self.start_node = None # Head pointer
        self.end_node = None # Tail pointer
        # Additional attributes
        self.index = index
        self.mode = "simple"

    # Method to traverse a created linked list
    def traverse_list(self):
        traversal = []
        if self.start_node is None:
            print("List has no element")
            return
        else:
            n = self.start_node
            # Start traversal from head, and go on till you reach None
            while n is not None:
                traversal.append(n.value)
                n = n.next
            return traversal

    # Method to insert elements in the linked list
    def insert_at_end(self, value):
        # determine data type of the value
        if 'list' in str(type(value)):
            self.mode = "list"

        # Initialze a linked list element of type "Node"
        new_node = Node(value)
        n = self.start_node # Head pointer

        # If linked list is empty, insert element at head
        if self.start_node is None:
            self.start_node = new_node
            self.end_node = new_node
            return "Inserted"

        elif self.mode == "list":
            if self.start_node.value[self.index] >= value[self.index]:
                self.start_node = new_node
                self.start_node.next = n
                return "Inserted"

            elif self.end_node.value[self.index] <= value[self.index]:
                self.end_node.next = new_node
                self.end_node = new_node
                return "Inserted"

            else:
                while value[self.index] > n.value[self.index] and value[self.index] < self.end_node.value[self.index] and n.next is not None:
                    n = n.next

                m = self.start_node
                while m.next != n and m.next is not None:
                    m = m.next
                m.next = new_node
                new_node.next = n
                return "Inserted"
        else:
            # If element to be inserted has lower value than head, insert new element at head
            if self.start_node.value >= value:
                self.start_node = new_node
                self.start_node.next = n
                return "Inserted"

            # If element to be inserted has higher value than tail, insert new element at tail
            elif self.end_node.value <= value:
                self.end_node.next = new_node
                self.end_node = new_node
                return "Inserted"

            # If element to be inserted lies between head & tail, find the appropriate position to insert it
            else:
                while value > n.value and value < self.end_node.value and n.next is not None:
                    n = n.next

                m = self.start_node
                while m.next != n and m.next is not None:
                    m = m.next
                m.next = new_node
                new_node.next = n
                return "Inserted"

if __name__ == '__main__':
    main()

Input ->  144285	Epidemiological and clinical characteristics of 136 cases of COVID-19 in main district of Chongqing

Doc id -> 144285
Doc text -> Epidemiological and clinical characteristics of 136 cases of COVID-19 in main district of Chongqing


Doc text post processing ->  epidemiological and clinical characteristics of 136 cases of covid-19 in main district of chongqing 

Doc tokens post whitespace tokenizing ->  ['epidemiological', 'and', 'clinical', 'characteristics', 'of', '136', 'cases', 'of', 'covid', '19', 'in', 'main', 'district', 'of', 'chongqing']
Doc tokens post stopword removal ->  ['epidemiological', 'clinical', 'characteristics', '136', 'cases', 'covid', '19', 'main', 'district', 'chongqing']
Doc tokens post stemming ->  ['epidemiolog', 'clinic', 'characterist', '136', 'case', 'covid', '19', 'main', 'district', 'chongq'] 

Input ->  74698	Late‐onset Pneumocystis jirovecii pneumonia post–fludarabine, cyclophosphamide and rituximab: implications for prophylaxis

Doc id 

Doc text post processing ->  ethical challenges arising in the covid-19 pandemic  an overview from the association of bioethics program directors  abpd  task force 

Doc tokens post whitespace tokenizing ->  ['ethical', 'challenges', 'arising', 'in', 'the', 'covid', '19', 'pandemic', 'an', 'overview', 'from', 'the', 'association', 'of', 'bioethics', 'program', 'directors', 'abpd', 'task', 'force']
Doc tokens post stopword removal ->  ['ethical', 'challenges', 'arising', 'covid', '19', 'pandemic', 'overview', 'association', 'bioethics', 'program', 'directors', 'abpd', 'task', 'force']
Doc tokens post stemming ->  ['ethic', 'challeng', 'aris', 'covid', '19', 'pandem', 'overview', 'associ', 'bioethic', 'program', 'director', 'abpd', 'task', 'forc'] 

Input ->  48538	Fever Screening and Detection of Febrile Arrivals at an International Airport in Korea: Association among Self-reported Fever, Infrared Thermal Camera Scanning, and Tympanic Temperature

Doc id -> 48538
Doc text -> Fever Scree

Doc tokens post stemming ->  ['analysi', 'hospit', 'acut', 'respiratori', 'diseas', 'recruit', 'immun', 'adenoviru', 'type', '4', '7', 'vaccin', '1', ''] 

Input ->  59615	Small Animal Literature Index

Doc id -> 59615
Doc text -> Small Animal Literature Index


Doc text post processing ->  small animal literature index 

Doc tokens post whitespace tokenizing ->  ['small', 'animal', 'literature', 'index']
Doc tokens post stopword removal ->  ['small', 'animal', 'literature', 'index']
Doc tokens post stemming ->  ['small', 'anim', 'literatur', 'index'] 

Input ->  62090	Emergency tracheal intubation: techniques and outcomes.

Doc id -> 62090
Doc text -> Emergency tracheal intubation: techniques and outcomes.


Doc text post processing ->  emergency tracheal intubation  techniques and outcomes  

Doc tokens post whitespace tokenizing ->  ['emergency', 'tracheal', 'intubation', 'techniques', 'and', 'outcomes', '']
Doc tokens post stopword removal ->  ['emergency', 'tracheal', 'intubation'

Doc text post processing ->  kardiologie 

Doc tokens post whitespace tokenizing ->  ['kardiologie']
Doc tokens post stopword removal ->  ['kardiologie']
Doc tokens post stemming ->  ['kardiologi'] 

Input ->  712	Estimating the risk of 2019 Novel Coronavirus death during the course of the outbreak in China, 2020

Doc id -> 712
Doc text -> Estimating the risk of 2019 Novel Coronavirus death during the course of the outbreak in China, 2020


Doc text post processing ->  estimating the risk of 2019 novel coronavirus death during the course of the outbreak in china  2020 

Doc tokens post whitespace tokenizing ->  ['estimating', 'the', 'risk', 'of', '2019', 'novel', 'coronavirus', 'death', 'during', 'the', 'course', 'of', 'the', 'outbreak', 'in', 'china', '2020']
Doc tokens post stopword removal ->  ['estimating', 'risk', '2019', 'novel', 'coronavirus', 'death', 'course', 'outbreak', 'china', '2020']
Doc tokens post stemming ->  ['estim', 'risk', '2019', 'novel', 'coronaviru', 'death', 'c


Doc text post processing ->  covid-19  review of epidemiology and potential treatments against 2019 novel coronavirus 

Doc tokens post whitespace tokenizing ->  ['covid', '19', 'review', 'of', 'epidemiology', 'and', 'potential', 'treatments', 'against', '2019', 'novel', 'coronavirus']
Doc tokens post stopword removal ->  ['covid', '19', 'review', 'epidemiology', 'potential', 'treatments', '2019', 'novel', 'coronavirus']
Doc tokens post stemming ->  ['covid', '19', 'review', 'epidemiolog', 'potenti', 'treatment', '2019', 'novel', 'coronaviru'] 

Input ->  84515	Impact of Non-cardiac Comorbidities in Adults with Congenital Heart Disease: Management of Multisystem Complications

Doc id -> 84515
Doc text -> Impact of Non-cardiac Comorbidities in Adults with Congenital Heart Disease: Management of Multisystem Complications


Doc text post processing ->  impact of non-cardiac comorbidities in adults with congenital heart disease  management of multisystem complications 

Doc tokens post wh

...

Doc text post processing ->  amphotericin b increases influenza a virus infection by preventing ifitm3-mediated restriction 

Doc tokens post whitespace tokenizing ->  ['amphotericin', 'b', 'increases', 'influenza', 'a', 'virus', 'infection', 'by', 'preventing', 'ifitm3', 'mediated', 'restriction']
Doc tokens post stopword removal ->  ['amphotericin', 'b', 'increases', 'influenza', 'virus', 'infection', 'preventing', 'ifitm3', 'mediated', 'restriction']
Doc tokens post stemming ->  ['amphotericin', 'b', 'increas', 'influenza', 'viru', 'infect', 'prevent', 'ifitm3', 'mediat', 'restrict'] 

Input ->  19214	Mapping of the RNA-binding domain of the porcine reproductive and respiratory syndrome virus nucleocapsid protein.

Doc id -> 19214
Doc text -> Mapping of the RNA-binding domain of the porcine reproductive and respiratory syndrome virus nucleocapsid protein.


Doc text post processing ->  mapping of the rna-binding domain of the porcine reproductive and respiratory syndrome virus nucle

Doc tokens post stemming ->  ['molecular', 'subtyp', 'reveal', 'immun', 'alter', 'idh', 'wild', 'type', 'lower', 'grade', 'diffus', 'glioma', ''] 

Input ->  90282	The Italian health system and the COVID-19 challenge

Doc id -> 90282
Doc text -> The Italian health system and the COVID-19 challenge


Doc text post processing ->  the italian health system and the covid-19 challenge 

Doc tokens post whitespace tokenizing ->  ['the', 'italian', 'health', 'system', 'and', 'the', 'covid', '19', 'challenge']
Doc tokens post stopword removal ->  ['italian', 'health', 'system', 'covid', '19', 'challenge']
Doc tokens post stemming ->  ['italian', 'health', 'system', 'covid', '19', 'challeng'] 

Input ->  36778	Gastritis might be considered as a technical factor affecting laparoscopic sleeve gastrectomy.

Doc id -> 36778
Doc text -> Gastritis might be considered as a technical factor affecting laparoscopic sleeve gastrectomy.


Doc text post processing ->  gastritis might be considered as a tech

Doc tokens post stemming ->  ['', 'organiz', 'impact', 'clinic', 'challeng', 'covid', '19', 'pandem', 'swiss', 'tertiari', 'intern', 'medicin', 'depart'] 

Input ->  24992	A novel anti-mycobacterial function of mitogen-activated protein kinase phosphatase-1

Doc id -> 24992
Doc text -> A novel anti-mycobacterial function of mitogen-activated protein kinase phosphatase-1


Doc text post processing ->  a novel anti-mycobacterial function of mitogen-activated protein kinase phosphatase-1 

Doc tokens post whitespace tokenizing ->  ['a', 'novel', 'anti', 'mycobacterial', 'function', 'of', 'mitogen', 'activated', 'protein', 'kinase', 'phosphatase', '1']
Doc tokens post stopword removal ->  ['novel', 'anti', 'mycobacterial', 'function', 'mitogen', 'activated', 'protein', 'kinase', 'phosphatase', '1']
Doc tokens post stemming ->  ['novel', 'anti', 'mycobacteri', 'function', 'mitogen', 'activ', 'protein', 'kinas', 'phosphatas', '1'] 

Input ->  113694	“The COVID-19 Generation”: A Cautionary No

Doc tokens post stemming ->  ['endovascular', 'manag', 'abdomin', 'aortic', 'aneurysm', 'year', 'review', ''] 

Input ->  76434	COVID-19 and Financial Vulnerability: What Health Care Organizations and Society Owe Each Other

Doc id -> 76434
Doc text -> COVID-19 and Financial Vulnerability: What Health Care Organizations and Society Owe Each Other


Doc text post processing ->  covid-19 and financial vulnerability  what health care organizations and society owe each other 

Doc tokens post whitespace tokenizing ->  ['covid', '19', 'and', 'financial', 'vulnerability', 'what', 'health', 'care', 'organizations', 'and', 'society', 'owe', 'each', 'other']
Doc tokens post stopword removal ->  ['covid', '19', 'financial', 'vulnerability', 'health', 'care', 'organizations', 'society', 'owe']
Doc tokens post stemming ->  ['covid', '19', 'financi', 'vulner', 'health', 'care', 'organ', 'societi', 'owe'] 

Input ->  135998	Helmet Modification to PPE With 3D Printing During the COVID-19 Pandemic at 

Input query ->  the novel coronavirus

Query Post Processing ->  the novel coronavirus
Doc tokens post whitespace tokenizing ->  ['the', 'novel', 'coronavirus']
Doc tokens post stopword removal ->  ['novel', 'coronavirus']
Doc tokens post stemming ->  ['novel', 'coronaviru'] 

Input query ->  from an epidemic to a pandemic

Query Post Processing ->  from an epidemic to a pandemic
Doc tokens post whitespace tokenizing ->  ['from', 'an', 'epidemic', 'to', 'a', 'pandemic']
Doc tokens post stopword removal ->  ['epidemic', 'pandemic']
Doc tokens post stemming ->  ['epidem', 'pandem'] 

Input query ->  is hydroxychloroquine effective?
Query Post Processing ->  is hydroxychloroquine effective 
Doc tokens post whitespace tokenizing ->  ['is', 'hydroxychloroquine', 'effective']
Doc tokens post stopword removal ->  ['hydroxychloroquine', 'effective']
Doc tokens post stemming ->  ['hydroxychloroquin', 'effect'] 

